In [18]:
import requests
from bs4 import BeautifulSoup

In [8]:
# https://www.bok.or.kr/portal/bbs/B0000245/list.do?menuNo=200761&pageIndex=31
url ='https://www.bok.or.kr/portal/bbs/B0000245/list.do?menuNo=200761'

def pageindex():
    pageIndex = []
    for i in range(1,31): #29P까지
        pageIndex.append (i)
    print (pageIndex)
    return pageIndex

In [9]:
import PyPDF2
import re

In [10]:
#pd.to_datetime()

# def date_format(d):

#     import datetime

#     d = str(d).replace('-', '.')

#     yyyy = int(d.split('.')[0])

#     mm = int(d.split('.')[1])

#     dd = int(d.split('.')[2])

#     this_date = datetime.date(yyyy, mm, dd)

#     return this_date

In [11]:
#pd.to_datetime()
def date_dot_format(d):

    import datetime

#   d = str(d).replace('-', '.')


    yyyy = int(d.split('.')[0])

    mm = int(d.split('.')[1])

    dd = int(d.split('.')[2])


    this_date = datetime.date(yyyy, mm, dd)

    return this_date

In [12]:
#pd.to_datetime()

# def int_to_date_format(d):

#     import datetime

#     yyyy = int(d[0:4])

#     mm = int(d[4:6])

#     dd = int(d[6:8])

#     this_date = datetime.date(yyyy, mm, dd)

#     return this_date

In [13]:
def read_text(path): #읽어들일 텍스트 파일 path # 텍스트 내용을 읽어서 반환
    f= open(path,'rt',encoding='UTF8') 
    content = f.read()
    f.close
    return content
    

In [14]:
def downloads_pdf(pdf_link,output_path): # (pdf 링크 , 저장할 path) pdf 다운로드 함수 
    file_res = requests.get(pdf_link)
    
    with open(output_path,'wb') as f: 
        f.write(file_res.content)


In [15]:
import re
from tika import parser
from os import listdir
from os.path import isfile, join
import shutil
# 폴더내 pdf파일을 txt 파일로 변경 ################ 폴더내 전체 pdf를 바꾸는 것임
def pdf3txt (source_folder, output_folder):
    error_list = []
    # 지정 폴더 내 파일 목록 조회 (파일만)
    pdf_files = [f for f in listdir(source_folder) if isfile(join(source_folder, f))]
    
    for pdf in pdf_files :
        pdf_tmp_filepath = source_folder + 'tmp.pdf'
        pdf_filepath = source_folder + pdf
        shutil.copyfile(pdf_filepath,pdf_tmp_filepath)



        # pdf 파일을 text로 변환
        print(pdf_filepath)
        try:
#             parsedPDF = re.sub('\n','',parser.from_file(pdf_tmp_filepath)['content'])
            parsedPDF = parser.from_file(pdf_tmp_filepath)['content']
        except:
            print(pdf)
            error_list.append(pdf)
            pass
        
        output_filepath = (output_folder+pdf).replace('.pdf','.txt')
        
        with open(output_filepath,'w',encoding = 'utf-8') as f:
            print(output_filepath)
            f.write(parsedPDF)
            f.close()

    return error_list

In [16]:
def bok():
    
    import re
    
    pageIndex= pageindex()
    bs_list = []
    
    for i in range(len(pageIndex)):

        url ='https://www.bok.or.kr/portal/bbs/B0000245/list.do?'

        params = ({
             'menuNo' : '200761',
             'pageIndex': pageIndex[i]
         })

        resp = requests.get(url,params)
        soup = BeautifulSoup(resp.content)

        find_soup = soup.find('div',class_ = 'bdLine type2')

        all_li_List = find_soup.find_all('li')

    #=================#print('all_li',len(all_li_List))========================================    
        find_li_List = []

        for j in range(len(all_li_List)):
            try :
                temp = all_li_List[j].find('div',class_ = "row")

                if temp:
                    find_li_List.append(temp) 

            except Exception:
                pass
        print(len(find_li_List))# 한페이지에 가져오는 리스트수
    #=============================================================       

        for j in range(len(find_li_List)):

            try:
                title_dates  = find_li_List[j].find('span',class_ = "titlesub").text
                upload_dates = find_li_List[j].find('span',class_ = "date").text
                pdf_link= find_li_List[j].find('div',class_ = "fileGoupBox").find('a')['href']
                pdf_title= find_li_List[j].find('div',class_ = "fileGoupBox").find('a').text
                
                
                li = title_dates.split('(')[2].split(')')[0]
                print(li)
                MPBDate = date_dot_format(li)
                print(MPBDate)        
        
    #===============링크처리, 저장할 path 지정=======================
                if pdf_title.find('pdf')== -1:
                    pdf_link = pdf_link[:len(pdf_link)-1]+'2'

                pdf_link = 'https://www.bok.or.kr'+pdf_link
                file_path = 'E:\\BOK\\{0}_{1}.pdf'.format(title_dates, upload_dates)
                file_result_path = 'E:\\BOK\\text2\\{0}_{1}.txt'.format(title_dates, upload_dates)
            except Exception:
                pass
    #===============pdf download=======================
#             downloads_pdf(pdf_link,file_path) #피디에프 다운로드 함수화
    #=================================================
            content = read_text(file_result_path)
    #=================파일로저장======================   
            bs_list.append({
                'Title Date':title_dates,
                'Upload Date':upload_dates,
                'pdf_link': pdf_link,
                'pdf_title':pdf_title,
                'MPBDate':MPBDate,
                'content':content
            })


    
    return bs_list
    



In [19]:
bok_list = bok()


[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30]
10
2019.6.20.
2019-06-20
2019.5.31.
2019-05-31
2019.5.9
2019-05-09
2019.4.18.
2019-04-18
2019.3.28.
2019-03-28
2019.2.28.
2019-02-28
2019.2.14.
2019-02-14
2019.1.24.
2019-01-24
2019.1.17.
2019-01-17
2018.12.26.
2018-12-26
10
2018.12.20.
2018-12-20
2018.12.6.
2018-12-06
2018.11.30.
2018-11-30
2018.11.8.
2018-11-08
2018.10.18.
2018-10-18
2018.9.20.
2018-09-20
2018.8.31.
2018-08-31
2018.7.26.
2018-07-26
2018.7.12.
2018-07-12
2018.6.20.
2018-06-20
10
2018.5.24.
2018-05-24
2018.4.26.
2018-04-26
2018.4.12.
2018-04-12
2018.3.29.
2018-03-29
2018.3.8.
2018-03-08
2018.2.27.
2018-02-27
2018.2.8.
2018-02-08
2018.1.18.
2018-01-18
2017.12.28.
2017-12-28
2017.12.14.
2017-12-14
10
2017.12.7.
2017-12-07
2017.11.30.
2017-11-30
2017.11.9.
2017-11-09
2017.10.19.
2017-10-19
2017.9.21.
2017-09-21
2017.8.31.
2017-08-31
2017.8.10.
2017-08-10
2017.7.13.
2017-07-13
2017.6.22.
2017-06-22
2017.5.25.
201

In [ ]:
# print(bok_list)
print(bok_list[1])
print(bok_list[28])
len(bok_list)


In [ ]:
bok_list[291] # list 0~ 291 번째 까지 (292개) 2019 ~ 2005.5 월

In [20]:
bok_list2005 = bok_list[:293]

In [ ]:
def write_all_list(path,list):
    f= open(path,'w',encoding='UTF8') 
    f.write(str(list))
    f.close

In [ ]:
#전체의사록 사전 txt 파일 하나로 합치기
all_path = 'E:\\BOK\\text2\\ALL_MPB.txt'
write_all_list(all_path,bok_list2005)

In [ ]:
# 파일 텍스트로 변환하는 함수 실행

pdf3txt ('E:\\BOK\\','E:\\BOK\\text2\\') 

# DataFrame 데이터 생성,파일 불러오기

In [2]:
import pandas as pd
import numpy as np

# test1_df = pd.read_csv(all_path)
# test1_df

In [ ]:
pd.read_csv?

In [23]:
# bok_list2005

[{'MPBDate': datetime.date(2019, 6, 20),
  'Title Date': '금융통화위원회 의사록(2019년도 제12차)(2019.6.20.)',
  'Upload Date': '등록일2019.07.09',
  'content': '\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n2019년도 제12차\n\n금융통화위원회(정기) 의사록\n\n한 국 은 행\n\n\n\n- 1 -\n\n1. 일 자 2019년 6월 20일(목)\n\n2. 장 소 금융통화위원회 회의실\n\n3. 출석위원 이 주 열 의 장(총재)\n\n이 일 형 위 원\n\n조 동 철 위 원\n\n고 승 범 위 원\n\n신 인 석 위 원\n\n윤 면 식 위 원(부총재)\n\n임 지 원 위 원\n\n4. 결석위원 없 음\n\n5. 참 여 자 장 호 현 감 사 허 진 호 부총재보\n\n신 호 순 부총재보 유 상 대 부총재보\n\n정 규 일 부총재보 이 승 헌 부총재보\n\n서 봉 국 외자운용원장 이 환 석 조사국장\n\n민 좌 홍 금융안정국장 박 종 석 통화정책국장\n\n이 상 형 금융시장국장 양 석 준 국제국장\n\n신 운 경제연구원장 김 현 기 공보관\n\n채 병 득 금융통화위원회실장 성 광 진 의사팀장\n\n6. 회의경과\n\n가. 의결안건\n\n<의안 제21호 – 금융안정보고서(2019년 6월)(안)>\n\n(１) 담당 부총재보가 한국은행법 제96조에 의거 금융안정보고서(2019년 6\n\n월)(안)을 의결하고자 한다는 내용의 제안설명을 하였음.\n\n(２) 위원 토의내용\n\n\n\n- 2 -\n\n제안설명에 이어 관련부서는 금번 보고서 작성의 기본방향과 위원협의회에서\n\n논의된 주요 내용을 다음과 같이 보고하였음.\n\n먼저 보고서 작성의 기본방향은 다음과 같음.\n\n보고서 체계는 지난해 하반기와 마찬가지로 부문별 금융안정 상황을 살

In [21]:
df = pd.DataFrame() # 빈 데이터 프레임을 만들어서 [{},{}...]전체 리스트 안에 사전형식으로된 MPB를 데이터 프레임화
for i in range(len(bok_list2005)):
    dftemp = pd.DataFrame(bok_list2005[i],index=[i])
    df = df.append(dftemp,ignore_index=True)
    

In [22]:
df

Title Date    Upload Date  \
0      금융통화위원회 의사록(2019년도 제12차)(2019.6.20.)  등록일2019.07.09   
1      금융통화위원회 의사록(2019년도 제10차)(2019.5.31.)  등록일2019.06.18   
2         금융통화위원회 의사록(2019년도 제9차)(2019.5.9)  등록일2019.05.28   
3       금융통화위원회 의사록(2019년도 제7차)(2019.4.18.)  등록일2019.05.07   
4       금융통화위원회 의사록(2019년도 제6차)(2019.3.28.)  등록일2019.04.12   
5       금융통화위원회 의사록(2019년도 제4차)(2019.2.28.)  등록일2019.03.19   
6       금융통화위원회 의사록(2019년도 제3차)(2019.2.14.)  등록일2019.03.05   
7       금융통화위원회 의사록(2019년도 제2차)(2019.1.24.)  등록일2019.02.12   
8       금융통화위원회 의사록(2019년도 제1차)(2019.1.17.)  등록일2019.02.07   
9    금융통화위원회 의사록(2018년도 제25차)(2018.12.26.)   등록일2019.01.15   
10   금융통화위원회 의사록(2018년도 제24차)(2018.12.20.)   등록일2019.01.08   
11     금융통화위원회 의사록(2018년도 제23차)(2018.12.6.)  등록일2018.12.26   
12    금융통화위원회 의사록(2018년도 제22차)(2018.11.30.)  등록일2018.12.18   
13    금융통화위원회 의사록(2018년도 제21차)(2018.11.8.)   등록일2018.11.27   
14    금융통화위원회 의사록(2018년도 제19차)(2018.10.18.)  등록일2018.11.06   
15    금융통화위원회 의사록(2018년도 제18차)(2018.9.20.)   등록일2018.10.10   
16    금융통화위원회 의사록(2018년도 제16차)(2018.8.31.)   등록일2018.09.18   
17    금융통화위원회 의사록(2018년도 제14차)(2018.7.26.)   등록일2018.08.14   
18    금융통화위원회 의사록(2018년도 제13차)(2018.7.12.)   등록일2018.07.31   
19    금융통화위원회 의사록(2018년도 제12차)(2018.6.20.)   등록일2018.07.06   
20    금융통화위원회 의사록(2018년도 제10차)(2018.5.24.)   등록일2018.06.12   
21      금융통화위원회 의사록(2018년도 제8차)(2018.4.26.)  등록일2018.05.15   
22      금융통화위원회 의사록(2018년도 제7차)(2018.4.12.)  등록일2018.05.02   
23      금융통화위원회 의사록(2018년도 제6차)(2018.3.29.)  등록일2018.04.17   
24       금융통화위원회 의사록(2018년도 제5차)(2018.3.8.)  등록일2018.03.27   
25      금융통화위원회 의사록(2018년도 제4차)(2018.2.27.)  등록일2018.03.20   
26       금융통화위원회 의사록(2018년도 제3차)(2018.2.8.)  등록일2018.02.27   
27      금융통화위원회 의사록(2018년도 제1차)(2018.1.18.)  등록일2018.02.06   
28    금융통화위원회 의사록(2017년도 제25차)(2017.12.28.)  등록일2018.01.16   
29    금융통화위원회 의사록(2017년도 제24차)(2017.12.14.)  등록일2018.01.02   
..                                      ...            ...   
263    금융통화위원회 의사록(2006년도 제22차)(2006.10.26)  등록일2006.12.12   
264    금융통화위원회 의사록(2006년도 제21차)(2006.10.12)  등록일2006.11.28   
265     금융통화위원회 의사록(2006년도 제20차)(2006.9.21)  등록일2006.11.07   
266      금융통화위원회 의사록(2006년도 제19차)(2006.9.7)  등록일2006.10.24   
267     금융통화위원회 의사록(2006년도 제18차)(2006.8.24)  등록일2006.10.10   
268     금융통화위원회 의사록(2006년도 제17차)(2006.8.17)  등록일2006.10.04   
269     금융통화위원회 의사록(2006년도 제16차)(2006.8.10)  등록일2006.09.26   
270      금융통화위원회 의사록(2006년도 제14차)(2006.7.7)  등록일2006.08.22   
271     금융통화위원회 의사록(2006년도 제13차)(2006.6.22)  등록일2006.08.08   
272      금융통화위원회 의사록(2006년도 제12차)(2006.6.8)  등록일2006.07.25   
273     금융통화위원회 의사록(2006년도 제11차)(2006.5.25)  등록일2006.07.11   
274     금융통화위원회 의사록(2006년도 제10차)(2006.5.11)  등록일2006.06.27   
275       금융통화위원회 의사록(2006년도 제8차)(2006.4.7)  등록일2006.05.23   
276      금융통화위원회 의사록(2006년도 제7차)(2006.3.23)  등록일2006.05.09   
277       금융통화위원회 의사록(2006년도 제6차)(2006.3.9)  등록일2006.04.25   
278       금융통화위원회 의사록(2006년도 제4차)(2006.2.9)  등록일2006.03.28   
279      금융통화위원회 의사록(2006년도 제3차)(2006.1.26)  등록일2006.03.14   
280      금융통화위원회 의사록(2006년도 제2차)(2006.1.12)  등록일2006.02.28   
281       금융통화위원회 의사록(2006년도 제1차)(2006.1.5)  등록일2006.02.21   
282    금융통화위원회 의사록(2005년도 제27차)(2005.12.22)  등록일2006.02.07   
283     금융통화위원회 의사록(2005년도 제26차)(2005.12.8)  등록일2006.01.24   
284    금융통화위원회 의사록(2005년도 제24차)(2005.11.10)  등록일2005.12.27   
285    금융통화위원회 의사록(2005년도 제21차)(2005.10.11)  등록일2005.11.29   
286     금융통화위원회 의사록(2005년도 제20차)(2005.9.22)  등록일2005.11.08   
287      금융통화위원회 의사록(2005년도 제19차)(2005.9.8)  등록일2005.10.25   
288     금융통화위원회 의사록(2005년도 제17차)(2005.8.11)  등록일2005.09.27   
289      금융통화위원회 의사록(2005년도 제14차)(2005.7.7)  등록일2005.08.23   
290     금융통화위원회 의사록(2005년도 제13차)(2005.6.23)  등록일2005.08.09   
291      금융통화위원회 의사록(2005년도 제12차)(2005.6.9)  등록일2005.07.26   
292     금융통화위원회 의사록(2005년도 제10차)(2005.5.12)  등록일2005.06.28   

                                              pdf_link  \
0    https://www.bok.or.kr/portal/cmmn/file/fileDow...   
1    https://www.bok.or.kr/portal/cmmn/file/fileDow...   
2    https://w

In [ ]:
df_MPB = df[['MPBDate','content']]

In [ ]:
df_MPB 

# csv 파일로 저장

In [ ]:
import pandas as pd
import numpy as np

df_MPB.to_csv('E:\\BOK\\text2\\ALL_MPB.csv',sep= " ")  #csv 파일로 저장

In [24]:
mpb_csv_test = pd.read_csv('E:\\BOK\\text2\\ALL_MPB.csv',sep= " ") #csv 파일 불러옴
mpb_csv_test

Unnamed: 0     MPBDate                                            content
0             0  2019-06-20  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
1             1  2019-05-31  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
2             2  2019-05-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
3             3  2019-04-18  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
4             4  2019-03-28  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
5             5  2019-02-28  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
6             6  2019-02-14  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
7             7  2019-01-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
8             8  2019-01-17  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
9             9  2018-12-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
10           10  2018-12-20  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
11           11  2018-12-06  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
12           12  2018-11-30  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
13           13  2018-11-08  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
14           14  2018-10-18  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
15           15  2018-09-20  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
16           16  2018-08-31  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
17           17  2018-07-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
18           18  2018-07-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
19           19  2018-06-20  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
20           20  2018-05-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
21           21  2018-04-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
22           22  2018-04-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
23           23  2018-03-29  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
24           24  2018-03-08  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
25           25  2018-02-27  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
26           26  2018-02-08  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
27           27  2018-01-18  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
28           28  2017-12-28  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
29           29  2017-12-14  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
..          ...         ...                                                ...
263         263  2006-10-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
264         264  2006-10-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
265         265  2006-09-21  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
266         266  2006-09-07  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
267         267  2006-08-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
268         268  2006-08-17  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
269         269  2006-08-10  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
270         270  2006-07-07  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
271         271  2006-06-22  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
272         272  2006-06-08  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
273         273  2006-05-25  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
274         274  2006-05-11  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
275         275  2006-04-07  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
276         276  2006-03-23  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
277         277  2006-03-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
278         278  2006-02-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
279         279  2006-01-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
280         280  2006-01-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
281         281  2006-01-05  \n\n\n\n\n\n\n\n\n\n\n\n\n

In [25]:
# 데이터 프레임 잘들어 있는지 전체 돌면서 검사하는 코드
# n = len(mpb_csv_test) - 10
# for i in range(len(mpb_csv_test)):
#     if i< n:
#         print(mpb_csv_test.iloc[i:i+10])

   Unnamed: 0     MPBDate                                            content
0           0  2019-06-20  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
1           1  2019-05-31  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
2           2  2019-05-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
3           3  2019-04-18  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
4           4  2019-03-28  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
5           5  2019-02-28  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
6           6  2019-02-14  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
7           7  2019-01-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
8           8  2019-01-17  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
9           9  2018-12-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
    Unnamed: 0     MPBDate                                            content
1            1  2019-05-31  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n.

    Unnamed: 0     MPBDate                                            content
32          32  2017-11-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
33          33  2017-10-19  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
34          34  2017-09-21  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
35          35  2017-08-31  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
36          36  2017-08-10  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
37          37  2017-07-13  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
38          38  2017-06-22  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
39          39  2017-05-25  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
40          40  2017-04-27  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
41          41  2017-04-13  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
    Unnamed: 0     MPBDate                                            content
33          33  2017-10-19  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n

    Unnamed: 0     MPBDate                                            content
59          59  2016-06-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
60          60  2016-05-13  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
61          61  2016-04-19  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
62          62  2016-03-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
63          63  2016-03-10  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
64          64  2016-02-25  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
65          65  2016-02-16  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
66          66  2016-01-28  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
67          67  2016-01-14  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
68          68  2015-12-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
    Unnamed: 0     MPBDate                                            content
60          60  2016-05-13  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n

    Unnamed: 0     MPBDate                                            content
84          84  2015-04-23  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
85          85  2015-04-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
86          86  2015-03-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
87          87  2015-03-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
88          88  2015-02-17  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
89          89  2015-01-29  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
90          90  2015-01-15  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
91          91  2014-12-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
92          92  2014-12-11  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
93          93  2014-11-13  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
    Unnamed: 0     MPBDate                                            content
85          85  2015-04-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n

116         116  2013-08-08  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
     Unnamed: 0     MPBDate                                            content
108         108  2014-01-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
109         109  2013-12-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
110         110  2013-12-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
111         111  2013-11-14  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
112         112  2013-10-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
113         113  2013-10-10  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
114         114  2013-09-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
115         115  2013-09-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
116         116  2013-08-08  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
117         117  2013-07-25  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
     Unnamed: 0     MPBDate                         

     Unnamed: 0     MPBDate                                            content
132         132  2012-10-25  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
133         133  2012-10-11  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
134         134  2012-09-27  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
135         135  2012-09-13  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
136         136  2012-08-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
137         137  2012-07-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
138         138  2012-07-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
139         139  2012-06-21  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
140         140  2012-06-08  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
141         141  2012-05-10  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
     Unnamed: 0     MPBDate                                            content
133         133  2012-10-11  \n\n\n\n\n\n\n\n\n\n\n\

     Unnamed: 0     MPBDate                                            content
158         158  2011-07-21  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
159         159  2011-07-14  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
160         160  2011-06-23  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
161         161  2011-06-10  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
162         162  2011-05-13  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
163         163  2011-04-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
164         164  2011-03-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
165         165  2011-03-10  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
166         166  2011-02-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
167         167  2011-02-11  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
     Unnamed: 0     MPBDate                                            content
159         159  2011-07-14  \n\n\n\n\n\n\n\n\n\n\n\

     Unnamed: 0     MPBDate                                            content
185         185  2010-04-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
186         186  2010-03-25  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
187         187  2010-03-11  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
188         188  2010-02-11  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
189         189  2010-01-21  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
190         190  2010-01-07  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
191         191  2010-01-08  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
192         192  2009-12-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
193         193  2009-12-10  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
194         194  2009-11-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
     Unnamed: 0     MPBDate                                            content
186         186  2010-03-25  \n\n\n\n\n\n\n\n\n\n\n\

     Unnamed: 0     MPBDate                                            content
224         224  2008-09-11  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
225         225  2008-08-07  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
226         226  2008-07-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
227         227  2008-07-10  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
228         228  2008-06-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
229         229  2008-06-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
230         230  2008-05-22  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
231         231  2008-05-08  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
232         232  2008-04-10  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
233         233  2008-03-20  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
     Unnamed: 0     MPBDate                                            content
225         225  2008-08-07  \n\n\n\n\n\n\n\n\n\n\n\

     Unnamed: 0     MPBDate                                            content
258         258  2007-01-05  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
259         259  2006-12-21  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
260         260  2006-12-07  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
261         261  2006-11-23  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
262         262  2006-11-09  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
263         263  2006-10-26  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
264         264  2006-10-12  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
265         265  2006-09-21  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
266         266  2006-09-07  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
267         267  2006-08-24  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...
     Unnamed: 0     MPBDate                                            content
259         259  2006-12-21  \n\n\n\n\n\n\n\n\n\n\n\